In [1]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import lightgbm as lgb

import warnings
warnings.filterwarnings("ignore")

%matplotlib inline

import re

import json
import csv
import random

In [2]:
with open('E:/Lab/Project/VN Legal Dataset Benchmark/Data/tvpl/baohiem.json', encoding="utf8") as f:
    baohiem = json.load(f) 

In [3]:
baohiem

[{'question': '1. Lương hưu đối với quân nhân, công an nhân dân đã chuyển ngành được tính như thế nào?',
  'answer': 'Tại Khoản 3 Điều 11 Nghị định 33/2016/NĐ-CP quy định như sau:  3. Người lao động quy định tại Khoản 1 và Khoản 2 Điều 2 Nghị định này đã chuyển sang ngạch công nhân, viên chức quốc phòng, công an, cơ yếu hoặc chuyển ngành sang làm việc trong biên chế tại các cơ quan nhà nước, tổ chức chính trị, tổ chức chính trị - xã hội, hưởng lương từ ngân sách nhà nước hoặc chuyển ngành sang doanh nghiệp thuộc đối tượng thực hiện chế độ tiền lương do Nhà nước quy định rồi mới nghỉ hưu thì cách tính lương hưu thực hiện như sau:  a) Trường hợp, người lao động chuyển ngành sang các ngành nghề không được hưởng phụ cấp thâm niên nghề và trong tiền lương tháng đóng bảo hiểm xã hội làm căn cứ tính lương hưu không có phụ cấp thâm niên nghề thì được lấy mức bình quân tiền lương tháng làm căn cứ đóng bảo hiểm xã hội tại thời Điểm nghỉ hưu, cộng thêm Khoản phụ cấp thâm niên nghề (nếu đã được hư

In [4]:
# def count_word_nay(text):
#     pattern = r'\b(này)\b'  # Using \b to match whole word "này"
#     matches = re.findall(pattern, text)
#     return len(matches)

In [2]:
def count_word_nay(text):
    pattern = r'\b(này|này|này)\b'  # Using \b to match whole word "này"
    matches = re.findall(pattern, text)
    return len(matches)

def split_input(input):
    input = input.replace("\n", " ")
    input = " ".join(input.split())
    return input.split(". ")

# Format: Something + rule_sub_law + something + rule_law + something + stop_regex

def get_law_name(input):
    stop_regex = "(\.|\;|\,|\)|Điều|điểm|khoản| quy định| này| thì| khi| Quy định| về| như sau| ngày| được| doanh nghiệp bảo hiểm| hướng dẫn| đóng bằng| hồ sơ| bảo hiểm tiền gửi| và các văn bản| mà| nguyên tắc| đối tượng| trách nhiệm| đối với người| \(| là một| bao gồm:| Căn cứ| hoặc 24| \- Các| 2\.| sẽ| nếu| nhưng| cũng| xác định| theo đó| đối vời trường hợp| đặt| chồng| của Thủ tướng| thực hiện| để được| 1\.| đã thống nhất| quy đinh| để nắm rõ| và thời gian| hết thời hạn| đang đóng| điều chỉnh| và các| với nội dung| và một số văn bản liên quan| và các văn bản hướng dẫn| là| người đủ|\:| trường hợp| và một số| tính cả| đang hưởng lương hưu| - Thời gian| gồm| tính cả| Trên đây| tạm hoãn gọi nhập ngũ| hoàn thiện| ưu tiên trong tuyển| tiếp nhận vào| chế độ| nay không đủ tiêu chuẩn| và văn bản hướng dẫn| do Hội đồng| hoặc các giấy tờ| của Chính phủ| vừa được| chỉ quy định| Thẻ bảo hiểm| thẻ bảo hiểm| hiện hành| và tiếp tục| sau thời gian| không được| vào ngày| từ ngày| vừa được| đã được| người lao động sẽ được| hoặc xây dựng| có hiệu lực| có quy định| và không thuộc| toà án từ chối| phải đảm bảo tiêu| và phải đáp ứng)" # Ending part to stop regex 
    # Cái 'này' hơi đần =))) 
    # catch = re.search(stop_regex, input)
    # if catch == None: return input
    # return input[:catch.start()] 
    exceptions = ["An toàn, vệ sinh lao động", "an toàn, vệ sinh lao động", "Khám bệnh, chữa bệnh", "Cán bộ, công chức", "Phòng, chống rửa tiền", "quản lý, sử dụng vốn", "Phòng, chống tham nhũng", "Phòng, chống nhiễm vi rút", "Nhập cảnh, xuất cảnh, quá cảnh, cư trú của người nước ngoài tại Việt Nam", "Thực hành tiết kiệm, chống lãng phí", "Phòng, chống bệnh truyền nhiễm"]
    for exception in exceptions:
        input = input.replace(exception, f"EXCEPTION-{exceptions.index(exception)}")
    
    catch = re.search(stop_regex, input)
    
    if catch is None:
        return input
    
    law_name = input[:catch.start()]
    
    for exception in exceptions:
        law_name = law_name.replace(f"EXCEPTION-{exceptions.index(exception)}", exception)
    
    return law_name

def get_law(input):
    # rule_law = "(BL|Bộ luật|Nghị quyết|Luật|Nghị định|Bộ luật|Luật|Pháp lệnh|Bộ luật|Nghị quyết|Bộ luật|luật|pháp lệnh|Pháp lệnh|Nghị định)"  
    rule_law = "(Nghị định|Thông tư liên tịch|Quyết định|Luật|Thông tư|Nghị quyết|Bộ luật|Pháp lệnh)"
    rule_sublaw = r"\b(?!điều kiện\b|Điều này\b|điểm mua\b|khoản tiền\b|điều hành\b|khoản đối\b|điều trị\b|điều hành\b|điểm thẻ\b|điểm dưới\b|điều chỉnh\b|điều của\b|Điều kiện\b|khoản chuyên thu\b|điều lệ\b|điểm giao\b|điểm đóng\b|điểm hành\b|điểm hưởng\b|điểm quy định tại\b|điểm thi\b|điểm sinh\b|điều tra\b|điểm để\b|điểm người\b|điểm nghỉ\b|điểm và\b|điểm Chủ tịch\b|điểm thân\b|khoản chi\b|khoản bổ sung\b|điểm cần lưu ý\b|điểm đi làm\b|khoản bị\b|khoản thanh\b|khoản thu\b|khoản phải chi\b|điểm của\b|điểm tài\b|điểm đặt\b|Điều lệ\b|khoản nợ\b|khoản dự phòng\b|điều kinh doanh\b|điều, khoản được giao\b|điểm kinh doanh\b|điểm Công\b|khoản ngoại tệ\b|khoản vay\b|khoản trả\b|khoản vốn\b|điểm đề\b|điểm trả\b|điểm từ\b|điểm cung\b|điểm chấm\b|khoản bảo\b|điểm kiểm tra\b|điểm thanh tra\b|điểm vi phạm\b|khoản, hạn mức\b|điểm công cộng\b|điều ước quốc tế\b|khoản cứu trợ\b|khoản đóng góp\b)(Điều|điều|Khoản|khoản|Điểm|điểm)\b" #Chú ý các trường hợp như điều kiện (k muốn bắt chữ điều)
    law_list = re.split(rule_law, input)
    law_output = []

    # print(law_list)

    for i in range(len(law_list)):
        if i == 0: continue
        local_law = law_list[i-1]
        if re.search(rule_law, law_list[i]) == None: continue
        local_sublaw = re.search(rule_sublaw, local_law)
        # if local_sublaw == None: continue # Không có điều, khoản là vứt ???

        # Nếu k có điểm điều khoản thì cút sublaw
        if local_sublaw == None: 
            local_subsublaw = get_law_name(law_list[i+1])
            local_sublaw_catch = law_list[i] + local_subsublaw
            law_output.append(local_sublaw_catch)

        # Có thì cho vào
        else:
            local_sublaw = local_sublaw.start()
            local_sublaw = local_law[local_sublaw:]
            local_subsublaw = get_law_name(law_list[i+1])
            local_sublaw_catch = local_sublaw + law_list[i] + local_subsublaw
            law_output.append(local_sublaw_catch)

        # local_sublaw = local_sublaw.start()
        # local_sublaw = local_law[local_sublaw:]
        # local_subsublaw = get_law_name(law_list[i+1])
        # local_sublaw_catch = local_sublaw + law_list[i] + local_subsublaw
        # law_output.append(local_sublaw_catch)
    return law_output



def replace_nay_with_previous_unit(text):
    # Define a regular expression pattern to match law names in the X/Y/Z format
    law_name_pattern1 = r'(?:Nghị định|Thông tư liên tịch|Quyết định|Thông tư|Nghị quyết)\s[\dA-Z\/\-Đđ]+[\dA-ZĐđ]*(?:\snăm\s\d{4})?'

    # Define a pattern to match law names that start with specific phrases like "Bộ luật" or "Luật"
    law_name_pattern2 = r'(?:Bộ luật|Luật)[\s\w-]+(?:\snăm\s\d{4})?'

    # Exception (nhu cai stop_regex)
    law_name_exception = "(Luật An toàn, vệ sinh lao động|Luật an toàn, vệ sinh lao động|Luật Khám bệnh, chữa bệnh|Luật Cán bộ, công chức|Luật Phòng, chống rửa tiền|Luật phòng, chống rửa tiền|Luật quản lý, sử dụng vốn|Luật Phòng, chống tham nhũng|Luật Phòng, chống nhiễm vi rút|Luật Nhập cảnh, xuất cảnh, quá cảnh, cư trú của người nước ngoài tại Việt Nam|Luật Thực hành tiết kiệm, chống lãng phí|Luật Phòng, chống bệnh truyền nhiễm)"

    # # Use the findall method to find all matches in the text using both patterns
    # matches1 = re.findall(law_name_pattern1, text)
    # matches2 = re.findall(law_name_pattern2, text)

    matches1 = re.findall(law_name_pattern1, text)
    if len(re.findall(law_name_exception, text)) == 0:
        matches2 = re.findall(law_name_pattern2, text)
    else:
        matches2 = re.findall(law_name_exception, text)

    # Combine the detected law names from both patterns
    matches = matches1 + matches2

    # print()
    # print(matches)
    # print()

    # Create a dictionary to store law name references
    law_references = {}

    # Iterate through the matches and add them to the dictionary with a simplified reference
    for law_name in matches:
        if "này" in law_name: continue # Không xét những cái có chữ này (QUAN TRỌNG)
        words = law_name.split()
        
        if words[0] == "Luật":
            simplified_reference = "Luật"
        else:
            simplified_reference = " ".join(words[:2])

        law_references[simplified_reference] = law_name

    # print(law_references)
    
    # Use regular expressions to find and replace references with 'này' without unnecessary punctuation
    for simplified_reference, law_name in law_references.items():
        # Create a pattern to match the simplified reference followed by "này"
        reference_pattern = re.compile(fr'\b{simplified_reference}\s*này\b', re.IGNORECASE)
        # Replace the references with the correct law name
        text = re.sub(reference_pattern, law_name + ' này', text)   #Still change it to ...(full) + này + to regex above
    
    return text


def replace_nay_with_previous_unit_2(text): #Cho điều/mục/khoản/điểm này
    
    # Điều... + 1 or số la mã
    pattern = r'(?:Điều|điều|Khoản|khoản|Điểm|điểm|Mục|mục)\s+(?:[IVXLCDM\d]+)'

    # Use the findall method to find all matches in the text using both patterns
    matches = re.findall(pattern, text)

    # print()
    # print(matches)
    # print()

    # Create a dictionary to store law name references
    law_references = {}

    # Iterate through the matches and add them to the dictionary with a simplified reference
    for law_name in matches:
        if "này" in law_name: continue # Không xét những cái có chữ này (QUAN TRỌNG)
        words = law_name.split()
        
        if words[0] == "Mục" or words[0] == "mục":
            simplified_reference = "Mục"
        elif words[0] == "Điều" or words[0] == "điều":
            simplified_reference = "Điều"
        elif words[0] == "Khoản" or words[0] == "khoản":
            simplified_reference = "Khoản"
        elif words[0] == "Điểm" or words[0] == "điểm":
            simplified_reference = "Điểm"

        law_references[simplified_reference] = law_name

    # print(law_references)
    
    # Use regular expressions to find and replace references with 'này' without unnecessary punctuation
    for simplified_reference, law_name in law_references.items():
        # Create a pattern to match the simplified reference followed by "này"
        reference_pattern = re.compile(fr'\b{simplified_reference}\s*này\b', re.IGNORECASE)
        # Replace the references with the correct law name
        text = re.sub(reference_pattern, law_name, text)   #K cần cái này để k bị bắt bởi cái stop regex ở treen
    
    # print()
    # print(text)

    return text

def cleaning_output(output):
    # Step 1: Remove trailing spaces
    text_list = [text.strip() for text in output]

    # Step 2: Remove duplicates
    text_list = list(set(text_list))

    filtered_text_list = text_list

    # Step 4: Remove "bạn nên tham khảo thêm tại " from the input text
    filtered_text_list = [text.replace("bạn nên tham khảo thêm tại ", "") for text in filtered_text_list]

    # Step 5: Function to clean the text (xóa và, hoặc,.. ở cuối câu)
    def clean_text(text):
        text = text.strip()  # Remove leading and trailing whitespace
        text = text.rstrip(" và").rstrip(" hoặc")  # Remove " và" or " hoặc" from the end of the text
        return text

    # Remove " và" or " hoặc" from each text item in the list
    filtered_text_list = [clean_text(text) for text in filtered_text_list]

    # Step 3: Remove entities that exactly match inside other entities
    def remove_sub_entities(text_list):
        # text_list.sort(key=len)  # Sort by length to process shorter entities first
        filtered_list = []

        for text in text_list:
            is_sub_entity = False
            for filtered_text in filtered_list:
                if text in filtered_text:
                    is_sub_entity = True
                    break
            if not is_sub_entity:
                filtered_list.append(text)

        return filtered_list

    filtered_text_list = remove_sub_entities(filtered_text_list)

    # Filter the list to retain only matching entities or entities with numbers
    filtered_text_list = [text if not text.startswith("Quyết định") else (text if re.search(r'\d', text) else None) for text in filtered_text_list]

    # Remove None values from the list
    filtered_text_list = [text for text in filtered_text_list if text is not None]


    # Step 6: Remove entities that are only "Luật" or "Nghị quyết"
    filtered_text_list = [entity for entity in filtered_text_list if entity not in ("Luật", "Nghị quyết")]

    return filtered_text_list


def run_get_law(input):
    # for unit in units_to_replace:
    #     input = replace_nay_with_previous_unit(input, unit)
    input = replace_nay_with_previous_unit(input) #Luật/ Thông tư/... này
    input = replace_nay_with_previous_unit_2(input) # Điều mục khoản này
    input = split_input(input)
    output = []
    for i in input:
        local = get_law(i)
        if len(local) == 0: continue
        output += local
    output = cleaning_output(output)
    return output

In [20]:
i = random.randint(0, len(baohiem))

print(i)

6737


In [21]:
text = baohiem[i]["answer"]

print(text)
print()
print("Này counter:", count_word_nay(text))
print()
print(run_get_law(text))

Nếu bà Hà nhập viện tại Bệnh viện đa khoa tỉnh Đồng Nai trong tình trạng cấp cứu thì sẽ được cơ quan BHXH chi trả như đối với bệnh nhân khám, chữa bệnh đúng tuyến.  Trường hợp bà Hà vào viện không trong tình trạng cấp cứu, có xuất trình thẻ BHYT, bà sẽ được cơ quan BHXH chi trả 30% tổng chi phí trong phạm vi quyền lợi BHYT (Bệnh viện đa khoa tỉnh Đồng Nai là bệnh viện hạng I).  Bà Hà cần mang giấy ra viện, hóa đơn thu viện phí đến cơ quan BHXH TP. Hồ Chí Minh để được hướng dẫn và giải quyết theo quy định.

Này counter: 0


[]

{}
[]


In [8]:
def get_law_name2(text):
    # Define a regular expression pattern to match the law name
    pattern = r'(?:Nghị định|Thông tư liên tịch|Quyết định|Luật|Thông tư|Nghị quyết)\s+([\d/]+/[\w-]+)\s*'
    # Search for the pattern in the input text
    match = re.search(pattern, text)  
    if match:
        return match.group(1)
    else:
        return ""

print(get_law_name("Nếu nắng mai ta k thấy đc nhau Luật kinh doanh bảo hiểm 2022  doanh nghiệp phải"))

Nếu nắng mai ta k thấy đc nhau Luật kinh doanh bảo hiểm 2022 


In [22]:
text2 = "Điều 32 Nghị định Tố tụng hình sự (nếu rằng) Điều 2 Nghị định này đã cho ta thấy abc. Khoản 1 điều 2 Nghị định này có đã cho lại "

print(run_get_law(text2))

# K có Nghị định tố tụng hình sự (sai format kệ đi =))


['Nghị định T']

{'Nghị định': 'Nghị định T'}
['Điều 32 Nghị định Tố tụng hình sự', 'Khoản 1 điều 2 Nghị định T', 'Điều 2 Nghị định T']


In [55]:
text3 = "Nếu nắng mai này ta k thấy đc nhau Luật kinh doanh bảo hiểm 2022  doanh nghiệp phải"

print(run_get_law(text3))


[]

{}
['Luật kinh doanh bảo hiểm 2022']


In [69]:
text4 = "Tại Điều 61  Luật Bảo hiểm xã hội 2014  quy định bảo lưu thời gian đóng bảo hiểm xã hội, cụ thể như sau: Bảo lưu thời gian đóng bảo hiểm xã hội Người lao động khi nghỉ việc mà chưa đủ điều kiện để hưởng lương hưu theo quy định tại Điều 54 và Điều 55 của Luật này hoặc chưa hưởng bảo hiểm xã hội một lần theo quy định tại Điều 60 của Luật này thì được bảo lưu thời gian đóng bảo hiểm xã hội. Theo đó, thời gian bạn đóng bảo hiểm xã hội sẽ được bảo lưu khi bạn chưa đủ điều kiện hưởng lương hưu hoặc chưa hưởng bảo hiểm xã hội một lần. Thế nên, nếu tháng 10 bạn có việc bận không thể rút bảo hiểm xã hội 1 lần thì thời gian đóng bảo hiểm xã hội sẽ được bảo lưu cho đến khi có nhu cầu hưởng bảo hiểm xã hội 1 lần. Khi không hưởng bảo hiểm xã hội 1 lần thì thời gian đóng bảo hiểm xã hội có được bảo lưu không? (Hình từ Internet)"

print(text4)
print()
print("Này counter:", count_word_nay(text4))
print()
print(run_get_law(text4))

Tại Điều 61  Luật Bảo hiểm xã hội 2014  quy định bảo lưu thời gian đóng bảo hiểm xã hội, cụ thể như sau: Bảo lưu thời gian đóng bảo hiểm xã hội Người lao động khi nghỉ việc mà chưa đủ điều kiện để hưởng lương hưu theo quy định tại Điều 54 và Điều 55 của Luật này hoặc chưa hưởng bảo hiểm xã hội một lần theo quy định tại Điều 60 của Luật này thì được bảo lưu thời gian đóng bảo hiểm xã hội. Theo đó, thời gian bạn đóng bảo hiểm xã hội sẽ được bảo lưu khi bạn chưa đủ điều kiện hưởng lương hưu hoặc chưa hưởng bảo hiểm xã hội một lần. Thế nên, nếu tháng 10 bạn có việc bận không thể rút bảo hiểm xã hội 1 lần thì thời gian đóng bảo hiểm xã hội sẽ được bảo lưu cho đến khi có nhu cầu hưởng bảo hiểm xã hội 1 lần. Khi không hưởng bảo hiểm xã hội 1 lần thì thời gian đóng bảo hiểm xã hội có được bảo lưu không? (Hình từ Internet)

Này counter: 2


['Luật Bảo hiểm xã hội 2014  quy định bảo lưu thời gian đóng bảo hiểm xã hội', 'Luật này hoặc chưa hưởng bảo hiểm xã hội một lần theo quy định tại Điều 60 c

In [60]:
text5 = "Điểm a điểm b điểm c khoản 1 mục II Luật Bảo hiểm xã hội cho biết mẹ gì đó. Ta cũng biết khoản này rất đẹp trai. Âu mai gót khoản 1 mục này đẹp trai vl"

print(text5)
print()
print("Này counter:", count_word_nay(text5))
print()
print(replace_nay_with_previous_unit_2(text5))

Điểm a điểm b điểm c khoản 1 mục II Luật Bảo hiểm xã hội cho biết mẹ gì đó. Ta cũng biết khoản này rất đẹp trai. Âu mai gót khoản 1 mục này đẹp trai vl

Này counter: 2

Điểm a điểm b điểm c khoản 1 mục II Luật Bảo hiểm xã hội cho biết mẹ gì đó. Ta cũng biết khoản 1 rất đẹp trai. Âu mai gót khoản 1 mục II đẹp trai vl


In [61]:
output =  [
            "Quyết định số 45/2011/QĐ-TTg của Thủ tướng Chính phủ",
            "Luật Bảo hiểm xã hội",
            "Khoản 1, Điều 50 của Luật Bảo hiểm xã hội",
            "Luật Bảo hiểm xã hội",
            "Luật Bảo hiểm xã hội 2023",
            "Quyết định",
            "Quyết định 29/THDT-XT năm 2923"
        ]

print(cleaning_output(output))

['Quyết định 29/THDT-XT năm 2923', 'Luật Bảo hiểm xã hội', 'Luật Bảo hiểm xã hội 2023', 'Khoản 1, Điều 50 của Luật Bảo hiểm xã hội', 'Quyết định số 45/2011/QĐ-TTg của Thủ tướng Chính phủ']


In [70]:
text6 = "Khoản 1 Luật An toàn, vệ sinh lao động quy định những gì hả Duy. Mình cũng k biết. Luật này"

print(text6)
print()
print("Này counter:", count_word_nay(text6))
print()
print(run_get_law(text6))

Khoản 1 Luật An toàn, vệ sinh lao động quy định những gì hả Duy. Mình cũng k biết. Luật này

Này counter: 1


['Luật An toàn, vệ sinh lao động']

{'Luật': 'Luật An toàn, vệ sinh lao động'}
['Luật An toàn, vệ sinh lao động', 'Khoản 1 Luật An toàn, vệ sinh lao động']


In [32]:
text7 = "Trường hợp doanh nghiệp bị đình chỉ chế độ ưu tiên khi thực hiện thủ tục hải quan được quy định tại Điều 22 Thông tư 72/2015/TT-BTC về chế độ ưu tiên trong thực hiện thủ tục hải quan, kiểm tra, giám sát hải quan đối với hàng hóa xuất, nhập khẩu của doanh nghiệp do Bộ Tài chính ban hành, theo đó:   1. Doanh nghiệp bị đình chỉ áp dụng chế độ ưu tiên trong các trường hợp sau:  a. Doanh nghiệp không còn đáp ứng một trong các điều kiện để áp dụng chế độ ưu tiên theo quy định tại Chương III Thông tư này;  b. Hết thời hạn tạm đình chỉ áp dụng chế độ ưu tiên mà doanh nghiệp không thực hiện các quy định tại Điều 45 Luật Hải quan;  c. Doanh nghiệp đề nghị dừng áp dụng chế độ ưu tiên.  2. Trường hợp doanh nghiệp đã bị đình chỉ áp dụng chế độ ưu tiên thì trong 02 (hai) năm tiếp theo, doanh nghiệp không được Tổng cục Hải quan xem xét, công nhận doanh nghiệp ưu tiên.  3. Quyết định đình chỉ theo mẫu 06/DNUT ban hành kèm theo Thông tư này.  Ngoài ra trường hợp doanh nghiệp bị đình chỉ chế độ ưu tiên khi thực hiện thủ tục hải quan được hướng dẫn bởi Điều 17 Quy trình ban hành kèm theo Quyết định 2659/QĐ-TCHQ.  Trên đây là tư vấn về trường hợp doanh nghiệp bị đình chỉ chế độ ưu tiên khi thực hiện thủ tục hải quan. Để biết thêm thông tin chi tiết bạn nên tham khảo tại Thông tư 72/2015/TT-BTC."

print(text7)
print()
print("Này counter:", count_word_nay(text7))
print()
print(run_get_law(text7))

Trường hợp doanh nghiệp bị đình chỉ chế độ ưu tiên khi thực hiện thủ tục hải quan được quy định tại Điều 22 Thông tư 72/2015/TT-BTC về chế độ ưu tiên trong thực hiện thủ tục hải quan, kiểm tra, giám sát hải quan đối với hàng hóa xuất, nhập khẩu của doanh nghiệp do Bộ Tài chính ban hành, theo đó:   1. Doanh nghiệp bị đình chỉ áp dụng chế độ ưu tiên trong các trường hợp sau:  a. Doanh nghiệp không còn đáp ứng một trong các điều kiện để áp dụng chế độ ưu tiên theo quy định tại Chương III Thông tư này;  b. Hết thời hạn tạm đình chỉ áp dụng chế độ ưu tiên mà doanh nghiệp không thực hiện các quy định tại Điều 45 Luật Hải quan;  c. Doanh nghiệp đề nghị dừng áp dụng chế độ ưu tiên.  2. Trường hợp doanh nghiệp đã bị đình chỉ áp dụng chế độ ưu tiên thì trong 02 (hai) năm tiếp theo, doanh nghiệp không được Tổng cục Hải quan xem xét, công nhận doanh nghiệp ưu tiên.  3. Quyết định đình chỉ theo mẫu 06/DNUT ban hành kèm theo Thông tư này.  Ngoài ra trường hợp doanh nghiệp bị đình chỉ chế độ

In [24]:
output1 = [
            "Điều 22 Nghị định 39/2014/NĐ-CP",
            "Luật",
            "Điểm a, b Khoản 1 Điều 21 Nghị định 39/2014/NĐ-CP",
            "Điểm c, đ Khoản 1 Điều 21 Nghị định 39/2014/NĐ-CP",
            "Điểm d Khoản 1 Điều 21 Nghị định 39/2014/NĐ-CP",
            "Điều 21 bạn nên tham khảo thêm tại Nghị định 39/2014/NĐ-CP"
]

print(cleaning_output(output1))

['Điều 22 Nghị định 39/2014/NĐ-CP', 'Điểm a, b Khoản 1 Điều 21 Nghị định 39/2014/NĐ-CP', 'Điểm c, đ Khoản 1 Điều 21 Nghị định 39/2014/NĐ-CP', 'Điểm d Khoản 1 Điều 21 Nghị định 39/2014/NĐ-CP', 'Điều 21 Nghị định 39/2014/NĐ-CP']


In [5]:
# Iterate through the data and add the relevant_laws attribute
for item in baohiem:
    item["relevant_laws"] = run_get_law(item["answer"])


['Nghị định 33/2016/NĐ-CP']

{'Nghị định': 'Nghị định 33/2016/NĐ-CP'}

['Thông tư liên tịch 01/2008/TTLT-BCA-BLĐTBXH-BTC-BNV']

{'Thông tư': 'Thông tư liên tịch 01/2008/TTLT-BCA-BLĐTBXH-BTC-BNV'}

['Quyết định 2355/QĐ-BHXH năm 2022']

{'Quyết định': 'Quyết định 2355/QĐ-BHXH năm 2022'}

['Quyết định 2355/QĐ-BHXH năm 2022', 'Bộ luật Hình sự']

{'Quyết định': 'Quyết định 2355/QĐ-BHXH năm 2022', 'Bộ luật': 'Bộ luật Hình sự'}

['Quyết định 2355/QĐ-BHXH năm 2022']

{'Quyết định': 'Quyết định 2355/QĐ-BHXH năm 2022'}

['Thông tư 69/2022/TT-BTC', 'Luật Kinh doanh bảo hiểm ngày 16 tháng 6 năm 2022 là một trong các loại chứng chỉ sau']

{'Thông tư': 'Thông tư 69/2022/TT-BTC', 'Luật': 'Luật Kinh doanh bảo hiểm ngày 16 tháng 6 năm 2022 là một trong các loại chứng chỉ sau'}

['Thông tư 69/2022/TT-BTC']

{'Thông tư': 'Thông tư 69/2022/TT-BTC'}

['Thông tư 69/2022/TT-BTC']

{'Thông tư': 'Thông tư 69/2022/TT-BTC'}

['Bộ luật Lao động 2019  có quy định về ngày nghỉ lễ', 'Bộ luật Lao động 2019  có quy đ

In [36]:
baohiem 

[{'question': '1. Lương hưu đối với quân nhân, công an nhân dân đã chuyển ngành được tính như thế nào?',
  'answer': 'Tại Khoản 3 Điều 11 Nghị định 33/2016/NĐ-CP quy định như sau:  3. Người lao động quy định tại Khoản 1 và Khoản 2 Điều 2 Nghị định này đã chuyển sang ngạch công nhân, viên chức quốc phòng, công an, cơ yếu hoặc chuyển ngành sang làm việc trong biên chế tại các cơ quan nhà nước, tổ chức chính trị, tổ chức chính trị - xã hội, hưởng lương từ ngân sách nhà nước hoặc chuyển ngành sang doanh nghiệp thuộc đối tượng thực hiện chế độ tiền lương do Nhà nước quy định rồi mới nghỉ hưu thì cách tính lương hưu thực hiện như sau:  a) Trường hợp, người lao động chuyển ngành sang các ngành nghề không được hưởng phụ cấp thâm niên nghề và trong tiền lương tháng đóng bảo hiểm xã hội làm căn cứ tính lương hưu không có phụ cấp thâm niên nghề thì được lấy mức bình quân tiền lương tháng làm căn cứ đóng bảo hiểm xã hội tại thời Điểm nghỉ hưu, cộng thêm Khoản phụ cấp thâm niên nghề (nếu đã được hư

In [6]:
# Define the output JSON file name
output_filename = "baohiem_fix5.json"

# Write the updated data to the output JSON file
with open(output_filename, "w", encoding="utf-8") as json_file:
    json.dump(baohiem, json_file, ensure_ascii=False, indent=4)

### Testing v3_data

In [3]:
with open('E:/Lab/Project/VN Legal Dataset Benchmark/Data/v3_data.json', encoding="utf8") as f:
    v3data = json.load(f) 

In [4]:
v3data

[{'href': 'https://thuvienphapluat.vn/hoi-dap-phap-luat/30F5B-hd-lai-suat-cho-vay-ho-tro-ho-ngheo-de-xay-dung-nha-o-phong-tranh-bao-lut-khu-vuc-mien-trung.html',
  'question': 'Lãi suất cho vay hỗ trợ hộ nghèo để xây dựng nhà ở phòng, tránh bão, lụt khu vực miền Trung được quy định như thế nào?',
  'answer': 'Lãi suất cho vay hỗ trợ hộ nghèo để xây dựng nhà ở phòng, tránh bão, lụt khu vực miền Trung được quy định tại Điều 5 Thông tư 41/2014/TT-NHNN hướng dẫn việc cho vay của Ngân hàng Chính sách xã hội theo Quyết định 48/2014/QĐ-TTg về chính sách hỗ trợ hộ nghèo xây dựng nhà ở phòng, tránh bão, lụt khu vực miền Trung do Thống đốc Ngân hàng Nhà nước ban hành. Cụ thể là:  Lãi suất cho vay áp dụng là 3%/năm.  Căn cứ nhu cầu vay vốn của hộ gia đình, Ngân hàng Chính sách xã hội xem xét và quyết định mức cho vay, nhưng không vượt quá 15 triệu đồng/hộ gia đình  Căn cứ quy định trên đây thì lãi suất cho vay hỗ trợ hộ nghèo để xây dựng nhà ở phòng, tránh bão, lụt khu vực miền Trung là 3%/năm.  

In [65]:
text8 = v3data[5462]["answer"]

print(text7)
print()
print("Này counter:", count_word_nay(text8))
print()
print(run_get_law(text8))

Trường hợp doanh nghiệp bị đình chỉ chế độ ưu tiên khi thực hiện thủ tục hải quan được quy định tại Điều 22 Thông tư 72/2015/TT-BTC về chế độ ưu tiên trong thực hiện thủ tục hải quan, kiểm tra, giám sát hải quan đối với hàng hóa xuất, nhập khẩu của doanh nghiệp do Bộ Tài chính ban hành, theo đó:   1. Doanh nghiệp bị đình chỉ áp dụng chế độ ưu tiên trong các trường hợp sau:  a. Doanh nghiệp không còn đáp ứng một trong các điều kiện để áp dụng chế độ ưu tiên theo quy định tại Chương III Thông tư này;  b. Hết thời hạn tạm đình chỉ áp dụng chế độ ưu tiên mà doanh nghiệp không thực hiện các quy định tại Điều 45 Luật Hải quan;  c. Doanh nghiệp đề nghị dừng áp dụng chế độ ưu tiên.  2. Trường hợp doanh nghiệp đã bị đình chỉ áp dụng chế độ ưu tiên thì trong 02 (hai) năm tiếp theo, doanh nghiệp không được Tổng cục Hải quan xem xét, công nhận doanh nghiệp ưu tiên.  3. Quyết định đình chỉ theo mẫu 06/DNUT ban hành kèm theo Thông tư này.  Ngoài ra trường hợp doanh nghiệp bị đình chỉ chế độ

In [5]:
# Iterate through the data and add the relevant_laws attribute
for item in v3data:
    item["relevant_laws"] = run_get_law(item["answer"])

In [67]:
# Define the output JSON file name
output_filename = "v3data_fix6.json"

# Write the updated data to the output JSON file
with open(output_filename, "w", encoding="utf-8") as json_file:
    json.dump(v3data, json_file, ensure_ascii=False, indent=4)